In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
import pandas as pd

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)

spark = SparkSession.builder.getOrCreate()

# Load Data

In [0]:
df_users_skills_preds = spark.read.parquet("dbfs:/FileStore/shared_uploads/kinani@campus.technion.ac.il/users_skills_embeddings_last-3.parquet")

# Processing the data, and get the embeddings for the skills using BERT

In [0]:
import ast
from pyspark.sql.types import MapType, LongType, StructType, StructField, StringType, ArrayType,DoubleType
from pyspark.sql.functions import explode, col, size
import json

def extract_list(dict_str):
    try:
        return ast.literal_eval(dict_str)
    except (SyntaxError, ValueError):
        dict_ = []
        return dict_

def string_to_doubles_list(string_list):
    return json.loads(string_list)

extract_dict_udf = udf(extract_list, MapType(StringType(), ArrayType(StringType())))
df_users_skills = df_users_skills_preds.withColumn('skills', extract_dict_udf(col('skills')))
vector_to_list_udf = udf(string_to_doubles_list, ArrayType(DoubleType()))
result = df_users_skills.withColumn("embedding", vector_to_list_udf("embedding"))
# result.count()

Out[60]: 3827

# Applying KNN on the embeddings which we got earlier, with the labels we have from Kmeans we did on the earlier on the users

We used KNN, so we can see which positions the users should be in (or fit), using the skills he have.

In [0]:
df = result.toPandas()
X = pd.DataFrame(df['embedding'].tolist()) 
y = pd.DataFrame(df['prediction'].tolist())
ids = pd.DataFrame(df['id'].tolist())
position = pd.DataFrame(df['position'].tolist())

In [0]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test, ids_train, ids_test, pos_train, pos_test = train_test_split(X, y, ids, position,test_size=0.03, random_state=42)

In [0]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import f1_score

knn = KNeighborsClassifier(n_neighbors=5)

knn.fit(X_train, y_train)

predictions_train = knn.predict(X_train)
f1score = f1_score(predictions_train, y_train,  average='weighted')
print(f'Train F1 Score: {f1score}')

predictions_test = knn.predict(X_test)
f1score = f1_score(predictions_test, y_test,  average='weighted')
print(f'Test F1 Score: {f1score}')

/databricks/python/lib/python3.9/site-packages/sklearn/neighbors/_classification.py:179: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return self._fit(X, y)
Train F1 Score: 0.8669323566000926
Test F1 Score: 0.8343746591572679


In [0]:
predictions = knn.predict(X)

# Save or Load the Model

In [0]:
from joblib import dump, load

model_path = "/dbfs/FileStore/shared_uploads/kinani@campus.technion.ac.il/knn_model.joblib"

dump(knn, model_path)

Out[67]: ['/dbfs/FileStore/shared_uploads/kinani@campus.technion.ac.il/knn_model.joblib']

In [0]:
knn_loaded = load('/dbfs/FileStore/shared_uploads/kinani@campus.technion.ac.il/knn_model.joblib')

# Saving the predictions and validation set

In [0]:
X_listed = pd.DataFrame({'features_list': X.values.tolist()})

In [0]:
preds_df = pd.DataFrame(predictions, columns=['knn_predictions'])
final_df = pd.concat([ids, X_listed, y, preds_df, position], axis=1)
final_df.columns = ['id', 'embeddings', 'Kmeans_prediction', 'knn_prediction', 'position']

In [0]:
knn_results = spark.createDataFrame(final_df)
knn_results.display()

id embeddings Kmeans_prediction knn_prediction position jessica-smith-a0566b93 List(-0.4899250268936157, 0.16703514754772186, -0.5166215300559998, 0.17313160002231598, 0.6263149976730347, 0.5004934072494507, -0.060165826231241226, 7.26226600818336E-4, 0.24073532223701477, -0.0020912655163556337, -1.6951717138290405, 0.16521240770816803, -0.23312248289585114, -0.012979120016098022, -1.0825921297073364, -0.0022934493608772755, -0.7397275567054749, -0.5717427134513855, 0.3960302472114563, 1.2762517929077148, 0.17359206080436707, 0.3162430226802826, 0.792852520942688, -0.4103715419769287, 0.3714672029018402, 0.27296575903892517, -0.2737768590450287, -1.2978016138076782, 0.858415961265564, -0.9524570107460022, -0.7771773934364319, -0.7911713123321533, 0.00752278883010149, 1.2609493732452393, -0.10489657521247864, -0.004241102375090122, 0.14105628430843353, -1.342736840248108, -0.18467631936073303, 0.3152656853199005, -0.994401752948761, -1.0488780736923218, 0.7850348949432373, 1.700634479522705, -1.4216768741607666, -0.3894529938697815, 0.7636420726776123, -0.5333959460258484, -0.7752357125282288, -0.008542853407561779, 0.029639359563589096, -0.20622803270816803, 0.5218974351882935, -0.09280796349048615, 0.3170643448829651, -0.10934964567422867, -0.6637383699417114, 0.09938167780637741, -0.4723775386810303, 0.8204373717308044, -0.06783509999513626, -1.5865368843078613, -0.29529932141304016, 0.18170583248138428, -0.7037476897239685, 0.1750229448080063, -0.3317253291606903, 0.9667280316352844, 0.6654918193817139, -0.5790303349494934, -0.06120796501636505, -0.6491411924362183, 0.5686972141265869, 0.4896053969860077, 0.2173696905374527, 0.11517038196325302, -1.6291508674621582, 0.3684808313846588, -1.040084958076477, 0.8894232511520386, 0.3596513569355011, -0.5243513584136963, -0.39351949095726013, -0.1513013243675232, -0.27027860283851624, -0.9777588248252869, 0.7712758779525757, 0.4919006824493408, -0.13866116106510162, 0.8451429605484009, -0.3026870787143707, 1.0698341131210327, -0.42588892579078674, 1.4179893732070923, 0.5562310814857483, -0.742638111114502, -1.7950913906097412, 0.7776938080787659, 0.35736212134361267, -0.6452181935310364, -1.0592952966690063, 0.3500620424747467, -0.46277275681495667, 0.016030875965952873, -0.8551586866378784, -0.503597617149353, -0.19903984665870667, -0.3694184422492981, -0.01779351383447647, -1.3747856616973877, 0.9058144092559814, 0.7914702296257019, -0.42399299144744873, 1.7054601907730103, 0.1829594373703003, -0.386298269033432, -1.0177150964736938, 0.018963437527418137, -0.3938811123371124, -0.4216412901878357, 0.191350519657135, 0.3376134932041168, -0.005625653546303511, -0.7573879957199097, 0.12074460834264755, -0.5072786211967468, -1.0039527416229248, 0.7447394132614136, 0.39185503125190735, -0.6817878484725952, -0.350841224193573, -0.5811614394187927, -0.8923618197441101, -0.2524792551994324, -0.07822273671627045, -1.0508393049240112, -0.31239816546440125, -0.614043653011322, 0.3078159987926483, 0.26279786229133606, 0.01625650003552437, 1.7860521078109741, -1.483410358428955, -0.6783772110939026, -0.4634380042552948, 0.7683160305023193, -0.4105924963951111, 0.252716600894928, -0.023335302248597145, -0.04614671692252159, 0.7169562578201294, 0.40353924036026, 1.2686095237731934, -1.0955837965011597, 1.1860803365707397, 1.4204577207565308, -0.7762531638145447, -0.5690693855285645, 0.35944080352783203, -0.08225452154874802, -0.3107433319091797, 0.5701850652694702, -0.2633311450481415, 1.393725872039795, 0.15576399862766266, -0.3140439987182617, 1.5699366331100464, 1.4134974479675293, 0.2787141501903534, 1.6887532472610474, -0.5121138095855713, 0.5997226238250732, 1.0718789100646973, 0.30243608355522156, -1.0153650045394897, -2.511101007461548, -0.08277270942926407, -0.6602213382720947, -2.0448741912841797, -0.6099971532821655, 1.0688599348068237, 0.10878171026706696, 0.5834930539131165, 0.9384650588035583, 0.13316282629966736, 1.2665520906448364, -0.47847872972488403, -0.2084214985370636, 0.0

In [0]:
ids_test.columns = ['id']
pos_test.columns = ['position']
ids_l = ids_test['id'].tolist()
pos_l = pos_test['position'].tolist()
d = list(zip(ids_l, pos_l))
val_df = spark.createDataFrame(d, schema=['id', 'original_pos'])
val_df.display()

id original_pos provida Non-Profit/Government Consultant and Professor, Looking to Consult or Profess in the DFW Metroplex! ferdinando-fred-balestriero-b4901b3a Team Coach/supervisor-Customer Service at Sitel terigeiger Business Process Consultant at United Healthcare kevin-shelton-24638263 IT Support Specialist, MRHT-1, Mental Health Care Provider, CRMA mia-andrade-71a917239 Human Resources Specialist at Versacarry erinahlholm Environmental Advocate & Aspiring Change Facilitator | Championing Sustainability, Justice, and Our Planet 🌎 adam-harden Insurance Agent at Adventure Insurance jiewei-ella-wang-b0a98957 Marketing Intern from Tidwell Swaim Law Firm roger-miller-7154b04a Chemical Engineer at M Consulting, LLC neil-p-039814122 SDE 1 @ AWS shubham-gupta-72a120244 Actively looking for New Data engineer/ Big data engineer positions krystal-king-74b79296 Transmission and Distribution System Operator at Southern California Edison (SCE) marc-goodman-23368766 Conyers Group, Managing Director cole-webb-b75163144 Process Automation at Sabic lukas-melissa-marie-86a648272 Portfolio Manager | Digital product and marketing | Financial Products and Services | ✨ Crypto, Web 3.0 advocate | AML-Fraud & Risk Specialist 👷‍♀️ aaron-stevenson-040948b Riding Instructor /Racing Coach (RR, FT, ADV, SuMo) and Founder of Veteran Outreach program nathan-holder-125b3374 Information Technology Professional snyderleasing Experienced Leasing Professional lou-ann-thompson-08849317 Director Of Operations at Therapy Brands kristin-lee-48964879 BSN, RN, CPN mohammed-aitelhoussine Senior IT Project Manager dylan-shields-11261787 Toolmaker at Elk County Machining karen-woiderski-cpc-a-cca-9b97b01b1 Certified Professional Coder lukas-myhan-37318034 Senior Data Engineer – Enterprise Data Warehouse at DocuSign john-eberle-31621b106 Co-Founder at BALA Nurse Shoes robert-scharpf-3a1a91198 Associate Professor of Oncology and Biostatistics, Co-Founder and Head of Data Science at Delfi Diagnostics colleen-haggerty-5878a91 SVP Bank of America david-jager-57a50045 Managing Director - Investments at Wells Fargo Advisors emilio-ugarte-9b301977 Bar Manager at Rivermarket Bar and Kitchen dillon-reyes-49043b244 Sales Manager at South Park Doggie, Inc. marlon-chisholm-b2050966 Supply Technician at US Army jason-perez-lcsw-23a57878 Psychotherapist surendra-puttagunta-09453a14 Director of Application and Data Services emilynbaldwin Executive Associate to the Deputy Secretary at Maryland Department of Agriculture stephen-rokey-jr-42828339 Desktop Support Technician at QCR Holdings, Inc. sally-nichols-64b77a10 Urban Design Planning Manager at City of Bellevue david-c-smith-ii-11106824 Property Manager at Fairway Management Group, LLC forsalerealty Real Estate Broker at For Sale Realty sijia-chen-8a05a459 TA and PR at Engineering for Kids Portland daniel-gretzinger-068724158 Research Analyst at Kessler Investment Group shana-neal-a4891b2b EVP, Chief People Officer at BD kyrstin-watanabe-49220853 VP, Celebrity Talent Management at Beach House Group fjmarques Private Detective alison-mackinnon-2a71b488 Psychotherapist: clinically and spiritually informed counseling justin-shahbaz-9027a320 School Principal at Alliance Richard Merkin Middle School elizabethcheshire Hotel Sales Professional higinio-covarrubias-518aa39 Director of Husbandry at Audubon Aquarium of the Americas david-huhn-109b2224 Sr. Category Manager at Keurig Dr Pepper tracy-cosentino-57b14b1b Director, Strategy, Insights & Analytics eric-consiglio-285b0b4a Stock Market Analyst mike-rose-944aba3 Crop Credit Manager at Phila. Coca-Cola tagmills Sr. Business Process Manager at Philips Healthcare tiffany-hayes-95229854 Account Examination Specialist 2 at Great Lakes Higher Education Corporation and Affiliates william-koon-3b7727129 Highly effective sales leader with a proven track record of sales leadership. Experienced capital equipment, software and business services solutions sales professional. emily-reeves-198097165 